In [2]:
import pandas as pd
import numpy as np

import os
import re

import matplotlib.pyplot as plt
import seaborn as sns
sns.set_style("darkgrid")

import keras
from keras import initializers, regularizers, constraints, optimizers, layers, callbacks

from keras.preprocessing import text, sequence

from keras.layers import Dense,Input,LSTM,Bidirectional,Activation,Conv1D,GRU
from keras.layers import Dropout,Embedding,GlobalMaxPooling1D, MaxPooling1D, Add, Flatten
from keras.layers import GlobalAveragePooling1D, GlobalMaxPooling1D, concatenate, SpatialDropout1D

from keras.callbacks import EarlyStopping,ModelCheckpoint
from keras.models import Model
from keras.optimizers import Adam
from keras.callbacks import Callback

from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score
from sklearn.metrics import roc_auc_score

print(keras.__version__)

2.4.3


In [2]:
# from google.colab import drive
# drive.mount('/content/drive', force_remount=True)

In [27]:
# Load dataset
def load_data():
    data =pd.read_csv("/content/drive/My Drive/Colab Notebooks/Data/tweet_covid_processing_file2.csv", engine='python')
    return data

In [28]:
tweet_df = load_data()
tweet_df.head(5)

Unnamed: 0  ...                                   tweet_lemmatized
0           0  ...                       MeNyrbie Phil Gahan Chrisitv
1           1  ...  advice Talk neighbour family exchange phone nu...
2           2  ...  Coronavirus Australia Woolworths give elderly ...
3           3  ...  My food stock one empty PLEASE panic THERE WIL...
4           4  ...  Me ready go supermarket COVID outbreak Not I p...

[5 rows x 9 columns]

In [29]:
tweet_df.drop('Unnamed: 0',inplace=True,axis = 1)

In [30]:
tweet_df= tweet_df.dropna()

In [31]:
X=tweet_df.drop('label',axis=1)

In [32]:
## Get the Dependent features
y=tweet_df['label']

In [39]:
max_features=2000001
max_len=100
sequence_input = Input(shape=(max_len, ))
embed_size=300

In [41]:
X_final = X['tweet_stemmed'].copy()

In [42]:
from imblearn.over_sampling import SMOTE
from collections import Counter

In [48]:
tokenizer = text.Tokenizer(num_words = max_features,lower = True)
tokenizer.fit_on_texts(X_final)
X=tokenizer.texts_to_sequences(X_final)
X=sequence.pad_sequences(X_final,maxlen=max_len)

ValueError: ignored

In [46]:
oversample = SMOTE()
X, y = oversample.fit_resample(X_final, y)

ValueError: ignored

**Train test split**

In [43]:
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(X_final, y, test_size=0.33, random_state=42)

**Fast text**

In [6]:
from urllib.request import urlopen
import gzip

In [7]:
file = gzip.open(urlopen('https://dl.fbaipublicfiles.com/fasttext/vectors-crawl/cc.en.300.vec.gz'))

Put the words in the dictionary index, and the vectors in the word value, it will take some time.

In [8]:
vocab_and_vectors = {}  
for line in file:
  values = line.split()
  word = values[0].decode('utf-8')
  vector = np.asarray(values[1:], dtype='float32')
  vocab_and_vectors[word] = vector

In [18]:
list(vocab_and_vectors.keys())[5]

')'

In [17]:
'</s>'

'</s>'

**Embedding matrix**

In [9]:
embedding_matrix = np.zeros((len(vocab_and_vectors) + 1, 300))
for i, word, in enumerate(vocab_and_vectors.keys()):
  embedding_vector = vocab_and_vectors.get(word)
  if embedding_vector is not None:
    embedding_matrix[i] = embedding_vector

In [10]:
embedding_matrix

array([[ 0.1059    , -0.0758    ,  0.0485    , ...,  0.18629999,
        -0.1191    , -0.0048    ],
       [ 0.125     , -0.1079    ,  0.0245    , ...,  0.2305    ,
        -0.0696    , -0.0215    ],
       [-0.0517    ,  0.074     , -0.0131    , ...,  0.237     ,
         0.0004    , -0.0042    ],
       ...,
       [ 0.0142    ,  0.023     , -0.0099    , ...,  0.0298    ,
        -0.0126    , -0.0086    ],
       [-0.0499    ,  0.0152    ,  0.0038    , ...,  0.0817    ,
         0.0367    ,  0.0368    ],
       [ 0.        ,  0.        ,  0.        , ...,  0.        ,
         0.        ,  0.        ]])

In [11]:
vocab_and_vectors

{'2000000': array([ 1.059e-01, -7.580e-02,  4.850e-02, -5.300e-03, -5.220e-02,
         8.060e-02, -7.220e-02, -2.040e-02, -5.240e-02,  8.000e-02,
        -6.300e-03,  3.070e-02,  1.820e-02, -0.000e+00,  4.400e-02,
        -3.940e-02,  4.770e-02, -9.390e-02,  4.160e-02,  5.100e-03,
        -2.410e-02,  2.000e-04,  1.038e-01, -5.640e-02,  2.950e-02,
         2.040e-02, -8.330e-02,  1.141e-01,  2.690e-02,  1.272e-01,
         1.434e-01,  2.860e-02, -1.860e-02, -4.500e-02, -7.000e-03,
        -7.020e-02, -3.480e-02,  1.210e-02,  5.710e-02, -3.500e-02,
        -8.200e-02, -6.750e-02,  8.210e-02, -5.770e-02, -6.200e-03,
        -2.440e-02,  3.940e-02, -5.950e-02, -4.970e-02, -3.320e-02,
         1.180e-01, -6.090e-02, -1.043e-01,  9.380e-02,  2.070e-02,
         5.110e-02, -2.990e-02, -2.160e-02, -1.320e-02,  2.630e-02,
         1.500e-02,  3.370e-02,  3.150e-02, -7.980e-02,  1.056e-01,
         5.270e-02,  4.510e-02, -3.000e-02, -2.520e-02,  4.390e-02,
         7.550e-02,  7.870e-02, -9.50

In [13]:
# LSTM Implimentation
from tensorflow.keras.layers import Embedding,SpatialDropout1D
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.models import Sequential
from tensorflow.keras.preprocessing.text import one_hot
from tensorflow.keras.layers import LSTM
from tensorflow.keras.layers import Dense
from keras.layers.convolutional import Conv1D  
from keras.optimizers import SGD
from keras.optimizers import Adam
from tensorflow.keras import optimizers

from keras.models import Sequential
from keras.layers import Embedding,Bidirectional, Dense,Dropout
from keras.layers import Dense, Activation, Flatten
from keras import layers
from sklearn.model_selection import StratifiedKFold
from tensorflow.keras.layers import Dropout

**Build the model**

In [18]:
#50328 only for glove
#2000001 only for Fasttext
max_features=2000001
max_len=100
sequence_input = Input(shape=(max_len, ))
embed_size=300

This is incomplete project since the programm has been crashed having the low RAM

In [ ]:
model=Sequential()
model.add(Embedding(max_features,300,weights=[embedding_matrix],trainable=True ))
model.add(SpatialDropout1D(0.4))
model.add(Bidirectional(LSTM(128)))
model.add(Dropout(0.2))
model.add(Dense(5,activation='softmax'))
#model2.add(Dense(1,activation='relu'))
adam = optimizers.Adam(lr=0.002, beta_1=0.9, beta_2=0.999, epsilon=1e-08, decay=0.0)
model.compile(loss='sparse_categorical_crossentropy',optimizer=adam,metrics=['accuracy'])